In [ ]:
#Import modules
import sys
from wavefile import WaveReader, WaveWriter
import numpy as np

In [ ]:
#Parameters
hop_size=10e-3 #10 ms
win_size=50e-3 #50 ms

In [ ]:
#Specify input wav file, output wav file (to store modified input audio), 
#and output features file (to save extracted features)

in_file = '\path\to\input\wav\file'
out_file = '\path\to\output\wav\file'
feat_file = '\path\to\output\features\file'

In [ ]:
#an empty list to store computed feature values
feat_vals=[]

In [ ]:
#main loop
with WaveReader(in_file) as r:
	#get window and hop sizes in samples
	win_len=int(r.samplerate*win_size)
	hop_len=int(r.samplerate*hop_size)
	
	#initialise data array of size win_len; successive frames of the audio will be pushed 
    #into this array from the right
	data=np.zeros([r.channels,win_len])
    
	with WaveWriter(out_file, channels=r.channels, samplerate=r.samplerate) as w :
		for frame in r.read_iter(size=hop_len):
			#first discard the starting hop_len samples
			#(using frame.size instead of hop_len to handle the last iteration 
            #where hop_len #samples may not be read. A fix: zero pad loaded frame)
			data[:r.channels,:(win_len-frame.size)]=data[:r.channels,frame.size:]
			data[:r.channels,win_len-frame.size:]=frame
			
			#Do some processing: perform operations on 'data' or 'frame'
			#(use 'frame' if modifying audio (e.g., filtering) and writing to output wav, else, 
            #use 'data' to compute short-time features (e.g., short-time energy))
            
			#example operations:
			frame*=0.5							#reducing amplitude of audio, performed on 'frame'
			feat_vals.append((data**2).sum())	#computing short-time energy, performed on 'data'
			
			#Write the audio frames to the output file
			w.write(frame)

In [ ]:
#Writing the feature values to a text file
times = np.arange(0, hop_size*len(feat_vals), hop_size)
feats = np.array((times, feat_vals)).T
np.savetxt(feat_file, feats, fmt="%.3f", delimiter='\t', header='Time\tFeature', comments='')